# CASO PRÁCTICO

### ASIGNATURA: VISUALIZACIÓN DE DATOS

### ALUMNO: BORJA BARRICARTE NAVAS

SECCIÓN DE IMPORTACIÓN DE LOS DATOS NECESARIOS

En primer lugar, se cargan las bibliotecas necesarias:

In [1]:
import pandas as pd
import numpy as np
import requests
import json
import sys
import altair as alt

El notebook de Python está realizado con la versión 5 de Altair. Para asegurar la correcta ejecucion de los comandos, se revisa la versión de Altair instalada. En caso de ser anterior a la versión "5.0.0rc3", se actualiza a la versión más reciente:

In [2]:
curr_version = alt.__version__

if curr_version != '5.0.0rc3':

    !{sys.executable} -m pip install altair

In [3]:
alt.__version__

'5.0.0rc3'

Carga de datos de la fuente de Red Eléctrica de España (REE)

Se definen varias funciones para la comunicación con la API, descarga de los datos en formato .json y estructuración correcta de los mismos en tablas de manera que puedan ser utilizadas posteriormente por Altair.

Función de importación para datos de potencias instaladas y energías generadas:

In [4]:
 def importar_REE_1(ano_inicio,codigo,time_trunc):
        
    vector_tiempos = np.arange(ano_inicio,2022,2,dtype=int)

    df_list = []

    for t in vector_tiempos:

        tiempo = 'start_date=' + str(t) + '-01-01T00:00&end_date=' + str(t+1) + '-12-31T23:59'
        url_link = 'https://apidatos.ree.es/es/datos/' + str(codigo) + '?' + str(tiempo) + '&time_trunc=' + str(time_trunc)
        r = requests.get(url_link)
        datos = r.json()

        df_parcial = pd.json_normalize(datos['included'],
                               record_path=['attributes','values'],
                               meta=[['attributes','title'],['attributes','type']])
                               
        df_list.append(df_parcial)

    return pd.concat(df_list, ignore_index=True)

Función de importación para datos de demanda de energía y tiempo de interrupción medio:

In [5]:
def importar_REE_2(ano_inicio,codigo,time_trunc):
        
    vector_tiempos = np.arange(ano_inicio,2022,2,dtype=int)

    df_list = []

    for t in vector_tiempos:

        tiempo = 'start_date=' + str(t) + '-01-01T00:00&end_date=' + str(t+1) + '-12-31T23:59'
        url_link = 'https://apidatos.ree.es/es/datos/' + str(codigo) + '?' + str(tiempo) + '&time_trunc=' + str(time_trunc)
        r = requests.get(url_link)
        datos = r.json()

        df_parcial = pd.json_normalize(datos['included'],
                               record_path=['attributes','values'])
                               
        df_list.append(df_parcial)

    return pd.concat(df_list, ignore_index=True)

Función de importación para datos de mercado (precios):

In [6]:
def importar_REE_3(ano_inicio,codigo,time_trunc):
        
    vector_tiempos = np.arange(ano_inicio,2022,2,dtype=int)

    df_list = []

    for t in vector_tiempos:

        tiempo = 'start_date=' + str(t) + '-01-01T00:00&end_date=' + str(t+1) + '-12-31T23:59'
        url_link = 'https://apidatos.ree.es/es/datos/' + str(codigo) + '?' + str(tiempo) + '&time_trunc=' + str(time_trunc)
        r = requests.get(url_link)
        datos = r.json()

        df_parcial = pd.json_normalize(datos['included'][3]['attributes']['content'],
                               record_path=['attributes','values'])
                               
        df_list.append(df_parcial)

    return pd.concat(df_list, ignore_index=True)

Función de importación para datos de kms de redes existentes e indisponibilidad de la red:

In [7]:
 def importar_REE_4(ano_inicio,codigo,time_trunc):
        
    vector_tiempos = np.arange(ano_inicio,2022,2,dtype=int)

    df_list = []

    for t in vector_tiempos:

        tiempo = 'start_date=' + str(t) + '-01-01T00:00&end_date=' + str(t+1) + '-12-31T23:59'
        url_link = 'https://apidatos.ree.es/es/datos/' + str(codigo) + '?' + str(tiempo) + '&time_trunc=' + str(time_trunc)
        r = requests.get(url_link)
        datos = r.json()

        df_parcial = pd.json_normalize(datos['included'],
                               record_path=['attributes','values'],
                               meta=[['attributes','title']])
                               
        df_list.append(df_parcial)

    return pd.concat(df_list, ignore_index=True)

Carga de datos de la fuente del Instituto Nacional de Estadística (INE)

Función de importación para datos del Producto Interior Bruto (PIB) nacional. Se considera Producto interior bruto a precios de mercado, oferta precios corrientes. Datos no ajustados a estacionalidad y calendario:

In [8]:
def importar_INE(ano_inicio,ano_fin,codigo):
    
    tiempo = str(ano_inicio) + '0101:' + str(ano_fin) + '0101'
    url_link = 'https://servicios.ine.es/wstempus/js/ES/DATOS_TABLA/' + str(codigo) + '?date=' + str(tiempo)
    r = requests.get(url_link)
    datos = r.json()

    df_result = pd.json_normalize(datos[0]['Data'])                       

    return df_result

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: POTENCIAS INSTALADAS

Se realiza, en primer lugar, un preprocesado de los datos importados y se definen grupos de categorías según la tecnología de la fuente de generación:

In [9]:
potencia = importar_REE_1(2015,'generacion/potencia-instalada','month')
potencia.columns = ['valor', 'porcentaje', 'fecha', 'tecnologia', 'tipo1']
potencia['valor'] = potencia['valor'].round()
potencia['porcentaje'] = potencia['porcentaje'].round(2)
potencia['fecha'] = pd.to_datetime(potencia['fecha'], utc=True)
potencia['fecha'] = potencia['fecha'] + pd.to_timedelta(2, 'h')
potencia['año'] = potencia['fecha'].dt.year
potencia['mes'] = potencia['fecha'].dt.month

def set_values(row, value):
    return value[row]

map_dictionary = {'Carbón': 'Térmica',
                  'Ciclo combinado': 'Térmica',
                  'Cogeneración': 'Térmica',
                  'Eólica': 'Eólica',
                  'Fuel + Gas': 'Térmica',
                  'Hidroeólica': 'Otras',
                  'Hidráulica': 'Hidráulica',
                  'Motores diésel': 'Térmica',
                  'Nuclear': 'Nuclear',
                  'Otras renovables': 'Otras',
                  'Potencia total': 'Potencia total',
                  'Residuos no renovables': 'Otras',
                  'Residuos renovables': 'Otras',
                  'Solar fotovoltaica': 'Solar',
                  'Solar térmica': 'Solar',
                  'Turbina de gas': 'Térmica',
                  'Turbina de vapor': 'Térmica',
                  'Turbinación bombeo': 'Hidráulica'}

potencia['tipo2'] = potencia['tecnologia'].apply(set_values, args =(map_dictionary, ))
potencia['variacion_tecnologia'] = (potencia.groupby(['tecnologia'])['valor'].pct_change().fillna(0)*100).round(2)

potencia.head()

valor  porcentaje                     fecha  tecnologia      tipo1   año  \
0  17008.0        0.16 2015-01-01 01:00:00+00:00  Hidráulica  Renovable  2015   
1  17010.0        0.16 2015-02-01 01:00:00+00:00  Hidráulica  Renovable  2015   
2  17010.0        0.16 2015-03-01 01:00:00+00:00  Hidráulica  Renovable  2015   
3  17010.0        0.16 2015-04-01 00:00:00+00:00  Hidráulica  Renovable  2015   
4  17010.0        0.16 2015-05-01 00:00:00+00:00  Hidráulica  Renovable  2015   

   mes       tipo2  variacion_tecnologia  
0    1  Hidráulica                  0.00  
1    2  Hidráulica                  0.01  
2    3  Hidráulica                  0.00  
3    4  Hidráulica                  0.00  
4    5  Hidráulica                  0.00

Se genera nueva información con la variación de la potencia instalada según la categoría de fuente de generación:

In [10]:
variacion_potencia = potencia.groupby(['fecha', 'tipo2']).agg(suma = pd.NamedAgg(column='valor', aggfunc=sum)).reset_index() 
variacion_potencia['variacion_tipo2'] = (variacion_potencia.groupby(['tipo2'])['suma'].pct_change().fillna(0)*100).round(2)

variacion_potencia.head()

fecha           tipo2      suma  variacion_tipo2
0 2015-01-01 01:00:00+00:00          Eólica   22915.0              0.0
1 2015-01-01 01:00:00+00:00      Hidráulica   19461.0              0.0
2 2015-01-01 01:00:00+00:00         Nuclear    7573.0              0.0
3 2015-01-01 01:00:00+00:00           Otras    1505.0              0.0
4 2015-01-01 01:00:00+00:00  Potencia total  104829.0              0.0

Se generan los gráficos:

In [11]:
graf1 = alt.Chart(potencia, title="Evolución potencia instalada por tipo de fuente").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('y', aggregate='sum', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tipo de fuente')
            ).transform_calculate(
                y='datum.valor/12',
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=350,
                height=300
            )

graf2 = alt.Chart(potencia, title="Evolución potencia instalada por tipo de fuente").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tipo de fuente')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=350,
                height=300
            )


output = graf1 | graf2
output.save('Evolución_potencia_instalada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [12]:
graf1 = alt.Chart(potencia, title="Evolución % potencia instalada por tipo de fuente").mark_area(
                color='goldenrod',
                opacity=0.3
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('% Potencia instalada')
                .stack("normalize"),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=350,
                height=300
            )

brush = alt.selection_interval(encodings=['x'])
background = graf1.add_params(brush)
selected = graf1.transform_filter(brush).mark_area(color='goldenrod')

output = background + selected | selected
output.save('Evolución_%_potencia_instalada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [13]:
graf1 = alt.Chart(potencia, title="Evolución % potencia instalada renovable").mark_area(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('% Potencia instalada')
                .stack("normalize"),
            alt.Color('tipo1', type='nominal')
                .title('Tipo de fuente')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=350,
                height=300
            )


output = graf1
output.save('Evolución_%_potencia_instalada_renovable.html')
output

alt.Chart(...)

In [14]:
graf1 = alt.Chart(potencia, title="Evolución potencia instalada de tipo térmica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal',  sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Térmica')
            ).properties(
                width=300,
                height=250
            )

graf2 = alt.Chart(potencia, title="Evolución potencia instalada eólica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Eólica')
            ).properties(
                width=300,
                height=250
            )
            

graf3 = alt.Chart(potencia, title="Evolución potencia instalada de tipo hidráulica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Hidráulica')
            ).properties(
                width=300,
                height=250
            )



graf4 = alt.Chart(potencia, title="Evolución potencia instalada de tipo solar").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Solar')
            ).properties(
                width=300,
                height=250
            )


graf5 = alt.Chart(potencia, title="Evolución potencia instalada nuclear").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Nuclear')
            ).properties(
                width=300,
                height=250
            )


graf6 = alt.Chart(potencia, title="Evolución potencia instalada de tipo 'otras'").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Otras')
            ).properties(
                width=300,
                height=250
            )


output = alt.vconcat(graf1, graf2, graf3, graf4, graf5, graf6).resolve_scale(color='independent').configure_view(stroke=None)
output.save('Evolución_potencia_instalada_por_tecnologia.html')
output

alt.VConcatChart(...)

In [15]:
selector = alt.selection_point(fields=['tipo2'], bind='legend')

graf1 = alt.Chart(variacion_potencia, title="Variación potencia instalada por tipo de fuente").mark_line(
                color='goldenrod',
                opacity=0.3
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('variacion_tipo2', type='quantitative')
                .title('% Variacion'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.2))
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Potencia total')}
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))

brush = alt.selection_interval(encodings=['x'])
background = graf1.add_params(brush, selector)
selected = graf1.transform_filter(brush).mark_line(color='goldenrod')

output = background + yrule + selected | selected
output.save('Variacion_potencia_instalada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [16]:
selector = alt.selection_point(fields=['tipo2'], bind='legend')

graf1 = alt.Chart(variacion_potencia, title="Variación anual potencia instalada por tipo de fuente").mark_bar().encode(
            alt.X('año', type='nominal')
                .title('Año'),
            alt.Y('var', type='quantitative')
                .title('% Variacion media'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_calculate(
                año='year(datum.fecha)',
            ).transform_aggregate(
                var='mean(variacion_tipo2)',
                groupby=['año', 'tipo2']
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Potencia total')}
            ).add_params(
                selector
            ).properties(
                width=350,
                height=300
            )


graf2 = alt.Chart(variacion_potencia, title="Variación anual potencia instalada por tipo de fuente").mark_line().encode(
            alt.X('año', type='nominal')
                .title('Año'),
            alt.Y('var', type='quantitative')
                .title('% Variacion media'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('var', op='sum', order='descending'))
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_calculate(
                año='year(datum.fecha)',
            ).transform_aggregate(
                var='mean(variacion_tipo2)',
                groupby=['año', 'tipo2']
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Potencia total')}
            ).add_params(
                selector
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))


output = graf1 + yrule | graf2 + yrule
output.save('Variacion_anual_potencia_instalada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: ENERGÍA GENERADA

Se realiza, en primer lugar, un preprocesado de los datos importados y se definen grupos de categorías según el tipo de la fuente de generación:

In [17]:
generacion = importar_REE_1(2015,'generacion/estructura-generacion','month')
generacion.columns = ['valor', 'porcentaje', 'fecha', 'tecnologia', 'tipo1']
generacion['valor'] = (generacion['valor']/1000).round()
generacion['porcentaje'] = generacion['porcentaje'].round(2)
generacion['fecha'] = pd.to_datetime(generacion['fecha'], utc=True)
generacion['fecha'] = generacion['fecha'] + pd.to_timedelta(2, 'h')
generacion['año'] = generacion['fecha'].dt.year
generacion['mes'] = generacion['fecha'].dt.month

map_dictionary = {'Carbón': 'Térmica',
                  'Ciclo combinado': 'Térmica',
                  'Cogeneración': 'Térmica',
                  'Eólica': 'Eólica',
                  'Fuel + Gas': 'Térmica',
                  'Hidroeólica': 'Otras',
                  'Hidráulica': 'Hidráulica',
                  'Motores diésel': 'Térmica',
                  'Nuclear': 'Nuclear',
                  'Otras renovables': 'Otras',
                  'Generación total': 'Generación total',
                  'Residuos no renovables': 'Otras',
                  'Residuos renovables': 'Otras',
                  'Solar fotovoltaica': 'Solar',
                  'Solar térmica': 'Solar',
                  'Turbina de gas': 'Térmica',
                  'Turbina de vapor': 'Térmica',
                  'Turbinación bombeo': 'Hidráulica'}


generacion['tipo2'] = generacion['tecnologia'].apply(set_values, args =(map_dictionary, ))
generacion['variacion_tecnologia'] = (generacion.groupby(['tecnologia'])['valor'].pct_change().fillna(0)*100).round(2)

generacion.head()

valor  porcentaje                     fecha  tecnologia      tipo1   año  \
0  2555.0        0.10 2015-01-01 01:00:00+00:00  Hidráulica  Renovable  2015   
1  3559.0        0.15 2015-02-01 01:00:00+00:00  Hidráulica  Renovable  2015   
2  3846.0        0.17 2015-03-01 01:00:00+00:00  Hidráulica  Renovable  2015   
3  2663.0        0.13 2015-04-01 00:00:00+00:00  Hidráulica  Renovable  2015   
4  2967.0        0.14 2015-05-01 00:00:00+00:00  Hidráulica  Renovable  2015   

   mes       tipo2  variacion_tecnologia  
0    1  Hidráulica                  0.00  
1    2  Hidráulica                 39.30  
2    3  Hidráulica                  8.06  
3    4  Hidráulica                -30.76  
4    5  Hidráulica                 11.42

Se genera nueva información con la variación de la energía generada según la categoría de fuente de generación:

In [18]:
variacion_generacion = generacion.groupby(['fecha', 'tipo2']).agg(suma = pd.NamedAgg(column='valor', aggfunc=sum)).reset_index() 
variacion_generacion['variacion_tipo2'] = (variacion_generacion.groupby(['tipo2'])['suma'].pct_change().fillna(0)*100).round(2)

variacion_generacion.head()

fecha             tipo2     suma  variacion_tipo2
0 2015-01-01 01:00:00+00:00            Eólica   4955.0              0.0
1 2015-01-01 01:00:00+00:00  Generación total  24592.0              0.0
2 2015-01-01 01:00:00+00:00        Hidráulica   2874.0              0.0
3 2015-01-01 01:00:00+00:00           Nuclear   5240.0              0.0
4 2015-01-01 01:00:00+00:00             Otras    564.0              0.0

Se genera nueva información sobre el factor de planta (capacity factor) según la categoría de fuente de generación. Para ello se combina información de potencias instaladas y energía generada:

In [19]:
FP = pd.merge(potencia, generacion, how ='inner', on =['fecha', 'tecnologia', 'tipo1', 'tipo2'])
FP['he'] = FP['valor_y'] /FP['valor_x']*1000
FP = FP[['fecha', 'tecnologia', 'tipo1', 'tipo2', 'he']]

FP.head()

fecha  tecnologia      tipo1       tipo2          he
0 2015-01-01 01:00:00+00:00  Hidráulica  Renovable  Hidráulica  150.223424
1 2015-02-01 01:00:00+00:00  Hidráulica  Renovable  Hidráulica  209.229865
2 2015-03-01 01:00:00+00:00  Hidráulica  Renovable  Hidráulica  226.102293
3 2015-04-01 00:00:00+00:00  Hidráulica  Renovable  Hidráulica  156.554968
4 2015-05-01 00:00:00+00:00  Hidráulica  Renovable  Hidráulica  174.426808

Se generan los gráficos:

In [20]:
selector = alt.selection_point(fields=['tipo2'], bind='legend')

graf1 = alt.Chart(generacion, title="Evolución energía generada por tipo de fuente").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).add_params(
                selector
            ).properties(
                width=320,
                height=300
            )

graf2 = alt.Chart(generacion, title="Evolución energía generada por tipo de fuente").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).add_params(
                selector
            ).properties(
                width=320,
                height=300
            )


output = graf1 | graf2
output.save('Evolución_energia_generada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [21]:
graf1 = alt.Chart(generacion, title="Evolución % energía generada por tipo de fuente").mark_area(
                color='goldenrod',
                opacity=0.3
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('% Energía generada')
                .stack("normalize"),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=350,
                height=300
            )

brush = alt.selection_interval(encodings=['x'])
background = graf1.add_params(brush)
selected = graf1.transform_filter(brush).mark_area(color='goldenrod')

output = background + selected | selected
output.save('Evolución_%_energia_generada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [22]:
graf1 = alt.Chart(generacion, title="Evolución % energía generada renovable").mark_area(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('% Energía generada')
                .stack("normalize"),
            alt.Color('tipo1', type='nominal')
                .title('Tipo de fuente')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=350,
                height=300
            )


output = graf1
output.save('Evolución_%_energia_generada_renovable.html')
output

alt.Chart(...)

In [23]:
graf1 = alt.Chart(generacion, title="Evolución energía generada de tipo térmica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal',  sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Térmica')
            ).properties(
                width=300,
                height=250
            )

graf2 = alt.Chart(generacion, title="Evolución energía generada eólica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Eólica')
            ).properties(
                width=300,
                height=250
            )

graf3 = alt.Chart(generacion, title="Evolución energía generada de tipo hidráulica").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Hidráulica')
            ).properties(
                width=300,
                height=250
            )

graf4 = alt.Chart(generacion, title="Evolución energía generada de tipo solar").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Solar')
            ).properties(
                width=300,
                height=250
            )

graf5 = alt.Chart(generacion, title="Evolución energía generada nuclear").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Nuclear')
            ).properties(
                width=300,
                height=250
            )

graf6 = alt.Chart(generacion, title="Evolución penergía generada de tipo 'otras'").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología')
            ).transform_filter(
                alt.FieldEqualPredicate(field='tipo2', equal='Otras')
            ).properties(
                width=300,
                height=250
            )

output = alt.vconcat(graf1, graf2, graf3, graf4, graf5, graf6).resolve_scale(color='independent').configure_view(stroke=None)
output.save('Evolución_energia_generada_por_tecnologia.html')
output

alt.VConcatChart(...)

In [24]:
selector = alt.selection_point(fields=['tipo2'], bind='legend')

graf1 = alt.Chart(variacion_generacion, title="Variación energía generada por tipo de fuente").mark_line(
                color='goldenrod',
                opacity=0.3
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('variacion_tipo2', type='quantitative')
                .title('% Variacion'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.2))
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Generación total')}
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))

brush = alt.selection_interval(encodings=['x'])
background = graf1.add_params(brush, selector)
selected = graf1.transform_filter(brush).mark_line(color='goldenrod')


output = background + yrule + selected | selected
output.save('Variacion_energia_generada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [25]:
selector = alt.selection_point(fields=['tipo2'], bind='legend')

graf1 = alt.Chart(variacion_generacion, title="Variación anual energía generada por tipo de fuente").mark_bar().encode(
            alt.X('año', type='nominal')
                .title('Año'),
            alt.Y('var', type='quantitative')
                .title('% Variacion media'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_calculate(
                año='year(datum.fecha)',
            ).transform_aggregate(
                var='mean(variacion_tipo2)',
                groupby=['año', 'tipo2']
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Generación total')}
            ).add_params(
                selector
            ).properties(
                width=350,
                height=300
            )


graf2 = alt.Chart(variacion_generacion, title="Variación anual energía generada por tipo de fuente").mark_line().encode(
            alt.X('año', type='nominal')
                .title('Año'),
            alt.Y('var', type='quantitative')
                .title('% Variacion media'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('var', op='sum', order='descending'))
                .title('Tipo de fuente'),
            opacity=alt.condition(selector, alt.value(0.9), alt.value(0.3))
            ).transform_calculate(
                año='year(datum.fecha)',
            ).transform_aggregate(
                var='mean(variacion_tipo2)',
                groupby=['año', 'tipo2']
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Generación total')}
            ).add_params(
                selector
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))


output = graf1 + yrule | graf2 + yrule
output.save('Variacion_anual_energia_generada_por_tipo_fuente.html')
output

alt.HConcatChart(...)

In [26]:
graf1 = alt.Chart(FP, title="Fuentes renovables/no renovables").mark_bar(
            ).encode(
            alt.X('tipo1', type='nominal')
                .title(''),
            alt.Y('fp', aggregate='sum', type='quantitative')
                .title('Factor de planta (%)'),
            ).transform_aggregate(
                he_mean='mean(he)',
                groupby=['tipo1']
            ).transform_calculate(
                fp='datum.he_mean*100/(365/12*24)'
            ).properties(
                width=50,
                height=300
            )

graf2 = alt.Chart(FP, title="Tipo de fuente").mark_bar(
            ).encode(
            alt.X('tipo2', type='nominal')
                .title(''),
            alt.Y('fp', aggregate='sum', type='quantitative')
                .title('Factor de planta (%)'),
            ).transform_aggregate(
                he_mean='mean(he)',
                groupby=['tipo2']
            ).transform_calculate(
                fp='datum.he_mean*100/(365/12*24)'
            ).properties(
                width=160,
                height=300
            )

graf3 = alt.Chart(FP, title="Tecnología").mark_bar(
            ).encode(
            alt.X('tecnologia', type='nominal')
                .title(''),
            alt.Y('fp', aggregate='sum', type='quantitative')
                .title('Factor de planta (%)'),
            ).transform_aggregate(
                he_mean='mean(he)',
                groupby=['tecnologia']
            ).transform_calculate(
                fp='datum.he_mean*100/(365/12*24)'
            ).properties(
                width=400,
                height=300
            )


output = graf1 | graf2 | graf3
output.save('Factor_planta.html')
output

alt.HConcatChart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: DEMANDA DE ELECTRICIDAD

Se realiza, en primer lugar, un preprocesado de los datos importados (datos de REE):

In [27]:
demanda = importar_REE_2(2015,'demanda/evolucion','month')
demanda.columns = ['valor', 'porcentaje', 'fecha']
demanda['valor'] = (demanda['valor']/1000).round()
demanda['variacion'] = (demanda['valor'].pct_change().fillna(0)*100).round(2)

demanda.head()

valor  porcentaje                          fecha  variacion
0  23851.0           1  2015-01-01T00:00:00.000+01:00       0.00
1  22079.0           1  2015-02-01T00:00:00.000+01:00      -7.43
2  22321.0           1  2015-03-01T00:00:00.000+01:00       1.10
3  19914.0           1  2015-04-01T00:00:00.000+02:00     -10.78
4  21024.0           1  2015-05-01T00:00:00.000+02:00       5.57

Se realiza, en segundo lugar, un preprocesado de los datos importados (datos del INE):

In [28]:
PIB = importar_INE(2015,2023,'30678')
PIB = PIB[['Fecha', 'Valor']]
PIB['Fecha'] = pd.to_datetime(PIB['Fecha'], unit='ms')
PIB.columns = ['fecha', 'valor']
PIB['valor'] = PIB['valor'].round()
PIB = PIB.sort_values('fecha')
PIB['variacion'] = (PIB['valor'].pct_change().fillna(0)*100).round(2)


PIB.head()

fecha     valor  variacion
32 2014-12-31 23:00:00  257357.0       0.00
31 2015-03-31 22:00:00  272258.0       5.79
30 2015-06-30 22:00:00  266501.0      -2.11
29 2015-09-30 22:00:00  281976.0       5.81
28 2015-12-31 23:00:00  265989.0      -5.67

Se generan los gráficos:

In [29]:
graf1 = alt.Chart(demanda, title="Comparación evolución demanda eléctrica - PIB").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía demandada (GWh)')
                .axis(titleColor='#5276A7')
            ).properties(
                width=350,
                height=300
            )

graf2 = alt.Chart(PIB, title="Comparación evolución demanda eléctrica - PIB").mark_line(
                color='#F18727',
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('PIB (Millones €)')
                .axis(titleColor='#F18727')
            ).properties(
                width=350,
                height=300
            )


output = alt.layer(graf1, graf2).resolve_scale(y='independent')
output.save('Comparacion_demanda_electrica_PIB.html')
output

alt.LayerChart(...)

In [30]:
graf1 = alt.Chart(demanda, title="Evolución demanda eléctrica").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Energía demandada (GWh)'),
            ).properties(
                width=350,
                height=300
            )

media = alt.Chart(demanda).mark_line(
                color='red',
                size=2
            ).transform_window(
                rolling_mean='mean(valor)',
            ).encode(
                x='fecha:T',
                y='rolling_mean:Q'
            )

area1 = alt.Chart().mark_rect(                    
                color='goldenrod',
                opacity=0.5
            ).encode(
                x=alt.value(210),
                x2=alt.value(318),
                y=alt.value(0,),
                y2=alt.value(300),
            ).interactive()

area2 = alt.Chart().mark_rect(                    
                color='goldenrod',
                opacity=0.5
            ).encode(
                x=alt.value(218),
                x2=alt.value(234),
                y=alt.value(0,),
                y2=alt.value(300),
            ).interactive()

graf2 = alt.Chart(demanda, title="Variación demanda eléctrica").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('variacion', type='quantitative')
                .title('% Variacion'),
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))


output = area1 + area2 + media + graf1 | graf2 + yrule
output.save('Demanda_electrica_COVID.html')
output

alt.HConcatChart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: PRECIOS DE LA ENERGÍA

Se realiza, en primer lugar, un preprocesado de los datos importados:

In [31]:
precios = importar_REE_3(2015,'mercados/componentes-precio-energia-cierre-desglose','month')
precios.columns = ['valor', 'porcentaje', 'fecha']
precios['valor'] = precios['valor'].round(1)
precios['variacion'] = (precios['valor'].pct_change().fillna(0)*100).round(2)

precios.head()

valor  porcentaje                          fecha  variacion
0   67.1           1  2015-01-01T00:00:00.000+01:00       0.00
1   58.8           1  2015-02-01T00:00:00.000+01:00     -12.37
2   56.7           1  2015-03-01T00:00:00.000+01:00      -3.57
3   59.5           1  2015-04-01T00:00:00.000+02:00       4.94
4   58.1           1  2015-05-01T00:00:00.000+02:00      -2.35

Se generan los gráficos:

In [32]:
graf1 = alt.Chart(precios, title="Evolución precio de la energía eléctrica").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('Precio electricidad (€/MWh)'),
            ).properties(
                width=350,
                height=300
            )

media = alt.Chart(precios).mark_line(
                color='red',
                size=2
            ).transform_window(
                rolling_mean='mean(valor)',
            ).encode(
                x='fecha:T',
                y='rolling_mean:Q'
            )

area = alt.Chart().mark_rect(
                color='red',
                size=2
            ).transform_window(
                rolling_mean='mean(valor)',
            ).encode(
                x='fecha:T',
                y='rolling_mean:Q'
            )

area = alt.Chart().mark_rect(                    
                color='goldenrod',
                opacity=0.5
            ).encode(
                x=alt.value(210),
                x2=alt.value(318),
                y=alt.value(0,),
                y2=alt.value(300),
            )

graf2 = alt.Chart(precios, title="Variación precio de la energía eléctrica").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('variacion', type='quantitative')
                .title('% Variacion'),
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))


output = area + graf1 + media  | graf2 + yrule
output.save('Precio_energia_electrica.html')
output

alt.HConcatChart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: CALIDAD DE SUMINISTRO (TIEMPO DE INTERRUPCIÓN MEDIO "TIM")

Se realiza, en primer lugar, un preprocesado de los datos importados:

In [33]:
tim = importar_REE_2(2015,'transporte/tiempo-interrupcion-medio-tim','month')
tim.columns = ['valor', 'porcentaje', 'fecha']
tim['valor'] = tim['valor'].round(3)
tim['variacion'] = (tim['valor'].pct_change().fillna(0)*100).round(2)

tim.head()

valor  porcentaje                          fecha  variacion
0  0.046           1  2015-01-01T00:00:00.000+01:00       0.00
1  0.000           0  2015-02-01T00:00:00.000+01:00    -100.00
2  0.042           1  2015-03-01T00:00:00.000+01:00        inf
3  0.011           1  2015-04-01T00:00:00.000+02:00     -73.81
4  0.048           1  2015-05-01T00:00:00.000+02:00     336.36

Se generan los gráficos:

In [34]:
graf1 = alt.Chart(tim, title="Evolución tiempo de interrupción medio").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('TIM (min)'),
            ).properties(
                width=320,
                height=300
            )

media = alt.Chart(tim).mark_line(
                color='red',
                size=2
            ).transform_window(
                rolling_mean='mean(valor)',
            ).encode(
                x='fecha:T',
                y='rolling_mean:Q'
            )

graf2 = alt.Chart(tim, title="Variación tiempo de interrupción medio").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('variacion', type='quantitative')
                .title('% Variacion'),
            ).properties(
                width=350,
                height=300
            )

yrule = alt.Chart().mark_rule(strokeDash=[12, 6], size=1, color="black").encode(y=alt.datum(0))


output = graf1 | graf2 + yrule
output.save('Tiempo_interrupcion_medio.html')
output

alt.HConcatChart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: CALIDAD DE SUMINISTRO (INDISPONIBILIDAD DE LA RED)

Se realiza, en primer lugar, un preprocesado de los datos importados y se agrupan las categorías de indisponibilidad:

In [35]:
indisp = importar_REE_4(2015,'transporte/indice-indisponibilidad','month')
indisp.columns = ['valor', 'porcentaje', 'fecha', 'tipo']
indisp['valor'] = indisp['valor'].round(2)
indisp['fecha'] = pd.to_datetime(indisp['fecha'], utc=True)
indisp['fecha'] = indisp['fecha'] + pd.to_timedelta(2, 'h')
indisp['año'] = indisp['fecha'].dt.year

map_dictionary = {'Programada por mantenimiento preventivo y predictivo': 'Programada',
                  'Programada por causas ajenas al mantenimiento': 'Programada',
                  'No programada debida a mantenimiento correctivo': 'No programada',
                  'No programada debida a circunstancias fortuitas': 'No programada',
                  'Causa de fuerza mayor o acciones de terceros': 'Fuerza mayor',
                  'Sin clasificar': 'Sin clasificar',
                  'Indisponibilidad mensual total de la red de transporte': 'Total'}

indisp['tipo2'] = indisp['tipo'].apply(set_values, args =(map_dictionary, ))

indisp.head()

valor  porcentaje                     fecha  \
0   0.04    0.022989 2015-01-01 01:00:00+00:00   
1   0.30    0.064795 2015-02-01 01:00:00+00:00   
2   0.69    0.123656 2015-03-01 01:00:00+00:00   
3   0.61    0.125257 2015-04-01 00:00:00+00:00   
4   0.74    0.128472 2015-05-01 00:00:00+00:00   

                                                tipo   año       tipo2  
0  Programada por mantenimiento preventivo y pred...  2015  Programada  
1  Programada por mantenimiento preventivo y pred...  2015  Programada  
2  Programada por mantenimiento preventivo y pred...  2015  Programada  
3  Programada por mantenimiento preventivo y pred...  2015  Programada  
4  Programada por mantenimiento preventivo y pred...  2015  Programada

Se generan los gráficos:

In [36]:
graf1 = alt.Chart(indisp, title="Evolución indisponibilidad de la red").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('y', aggregate='sum', type='quantitative')
                .title('Indisponibilidad (%)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Categoría')
            ).transform_calculate(
                y='datum.valor/12',
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Total')}
            ).properties(
                width=350,
                height=300
            )

graf2 = alt.Chart(indisp, title="Evolución indisponibilidad de la red").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Indisponibilidad (%)'),
            alt.Color('tipo2', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Categoría')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Total')}
            ).properties(
                width=350,
                height=300
            )


output = graf1 | graf2
output.save('Indisponibilidad_red.html')
output

alt.HConcatChart(...)

In [37]:
graf1 = alt.Chart(indisp, title="Evolución % indisponibilidad de la red por categoría").mark_area(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('% contribución categoría')
                .stack("normalize"),
            alt.Color('tipo2', type='nominal')
                .title('Categoría')
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tipo2', equal='Total')}
            ).properties(
                width=350,
                height=300
            )


output = graf1
output.save('Indisponibilidad_red_%_categoria.html')
output

alt.Chart(...)

SECCIÓN DE TRATAMIENTO DE DATOS Y REPRESENTACION DE INFORMACIÓN: KILOMETROS DE LÍNEAS INSTALADOS

Se realiza, en primer lugar, un preprocesado de los datos importados:

In [38]:
kms = importar_REE_4(2015,'transporte/kilometros-lineas','year')
kms.columns = ['valor', 'porcentaje', 'fecha', 'tipo']
kms['valor'] = kms['valor'].round()
kms['variacion'] = (kms.groupby(['tipo'])['valor'].pct_change().fillna(0)*100).round(2)
kms['fecha'] = pd.to_datetime(kms['fecha'], utc=True)
kms['fecha'] = kms['fecha'] + pd.to_timedelta(2, 'h')
kms['año'] = kms['fecha'].dt.year

kms.head()

valor  porcentaje                     fecha                         tipo  \
0  21191.0    0.490358 2015-01-01 02:00:00+00:00      km de circuito a 400 kV   
1  21626.0    0.492930 2016-01-01 02:00:00+00:00      km de circuito a 400 kV   
2  19576.0    0.452984 2015-01-01 02:00:00+00:00      km de circuito a 220 kV   
3  19669.0    0.448322 2016-01-01 02:00:00+00:00      km de circuito a 220 kV   
4   2448.0    0.056658 2015-01-01 02:00:00+00:00  km de circuito hasta 132 kV   

   variacion   año  
0       0.00  2015  
1       2.05  2016  
2       0.00  2015  
3       0.48  2016  
4       0.00  2015

Se generan los gráficos:

In [39]:
graf1 = alt.Chart(kms, title="Evolución kilometros de líneas instalados").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('valor', type='quantitative')
                .title('kilómetros instalados (km)'),
            alt.Color('tipo', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Nivel de tensión')
            ).transform_calculate(
                y='datum.valor/12',
            ).properties(
                width=320,
                height=300
            )

graf2 = alt.Chart(kms, title="Evolución kilometros de líneas instalados").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('kilómetros instalados (km)'),
            alt.Color('tipo', type='nominal', sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Nivel de tensión')
            ).properties(
                width=320,
                height=300
            )


output = graf1 | graf2
output.save('kms_lineas.html')
output

alt.HConcatChart(...)

In [40]:
graf1 = alt.Chart(kms, title="Evolución % kilometros instalados").mark_area(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Fecha'),
            alt.Y('valor', type='quantitative')
                .title('% kilómetros instalados')
                .stack("normalize"),
            alt.Color('tipo', type='nominal')
                .title('Nivel de tensión')
            ).properties(
                width=350,
                height=300
            )


output = graf1
output.save('kms_lineas_%_categoria.html')
output

alt.Chart(...)

INTEGRACIÓN DE VISUALIZACIONES PARCIALES EN DASHBOARDS INTERACTIVOS

Dashboard para datos de potencia instalada:

In [41]:
selection_tecnologia = alt.selection_point(fields=['tipo2'])
selection_ano = alt.selection_point(fields=['año'])


graf11 = alt.Chart(potencia, title="Evolución potencia").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('y', aggregate='sum', type='quantitative')
                .title('Potencia instalada (MW)')
                .sort(field='tipo2', op='sum'),
            color = alt.condition(selection_tecnologia, 'tipo2:N', alt.value('lightgray'), title='Tipo de fuente'),
            order=alt.Order('tipo2').sort("ascending"),
            tooltip='tipo2'
            ).transform_calculate(
                y='datum.valor/12',
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).add_params(
                selection_tecnologia, selection_ano
            ).properties(
                width=270,
                height=200
            )


graf12 = alt.Chart(potencia, title="Evolución por tipo de fuente").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Año'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Potencia instalada (MW)'),
            color = alt.condition(selection_tecnologia, 'tipo2:N', alt.value('lightgray'), title='Tipo de fuente'),
            tooltip='tipo2'
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=270,
                height=200
            )


graf13 = alt.Chart(potencia, title="% por tipo de fuente").mark_arc(innerRadius=30).encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Potencia intalada (MW)'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            tooltip='tipo2'
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=160,
                height=200
            )


graf21 = alt.Chart(potencia, title="Evolución por tecnología").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Año'),
            alt.Y('valor', type='quantitative')
                .title('Potencia instalada (MW)'),
            alt.Color('tecnologia', type='nominal',  sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología'),
            tooltip='tecnologia'
            ).transform_filter(
                selection_tecnologia
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=270,
                height=200
            )


graf22 = alt.Chart(potencia, title="% por tecnología").mark_arc(innerRadius=30).encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Potencia intalada (MW)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología'),
                tooltip='tecnologia'
            ).transform_filter(
                selection_tecnologia
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=160,
                height=200
            )
    
    
graf23 = alt.Chart(potencia, title="% renovable").mark_arc().encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Potencia intalada (MW)'),
            alt.Color('tipo1', type='nominal')
                .title('Renovable')
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Potencia total')}
            ).properties(
                width=160,
                height=200
            )   
    
    

output = alt.vconcat(
    alt.hconcat(graf11, graf12, graf13), 
    alt.hconcat(alt.hconcat(graf21, graf22),graf23).resolve_scale(color='independent')
).resolve_scale(color='independent')
output.save('Dashboard_potencia_instalada.html')
output

alt.VConcatChart(...)

Dashboard para datos de energía generada:

In [42]:
selection_tecnologia = alt.selection_point(fields=['tipo2'])
selection_ano = alt.selection_point(fields=['año'])


graf11 = alt.Chart(generacion, title="Evolución energía").mark_bar(
            ).encode(
            alt.X('año', type='ordinal')
                .title('Año'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Energía generada (GWh)')
                .sort(field='tipo2', op='sum'),
            color = alt.condition(selection_tecnologia, 'tipo2:N', alt.value('lightgray'), title='Tipo de fuente'),
            order=alt.Order('tipo2').sort("ascending"),
            tooltip='tipo2'
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).add_params(
                selection_tecnologia, selection_ano
            ).properties(
                width=270,
                height=200
            )


graf12 = alt.Chart(generacion, title="Evolución por tipo de fuente").mark_line(
            ).encode(
            alt.X('fecha', type='temporal')
                .title('Año'),
            alt.Y('valor', aggregate='sum', type='quantitative')
                .title('Energía generada (GWh)'),
            color = alt.condition(selection_tecnologia, 'tipo2:N', alt.value('lightgray'), title='Tipo de fuente'),
            tooltip='tipo2'
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=270,
                height=200
            )


graf13 = alt.Chart(generacion, title="% por tipo de fuente").mark_arc(innerRadius=30).encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Energía generada (GWh)'),
            alt.Color('tipo2', type='nominal')
                .title('Tipo de fuente'),
            tooltip='tipo2'
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=160,
                height=200
            )


graf21 = alt.Chart(generacion, title="Evolución por tecnología").mark_line().encode(
            alt.X('fecha', type='temporal')
                .title('Año'),
            alt.Y('valor', type='quantitative')
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal',  sort=alt.EncodingSortField('valor', op='sum', order='descending'))
                .title('Tecnología'),
            tooltip='tecnologia'
            ).transform_filter(
                selection_tecnologia
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=270,
                height=200
            )


graf22 = alt.Chart(generacion, title="% por tecnología").mark_arc(innerRadius=30).encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Energía generada (GWh)'),
            alt.Color('tecnologia', type='nominal')
                .title('Tecnología'),
            tooltip='tecnologia'
            ).transform_filter(
                selection_tecnologia
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=160,
                height=200
            )
    
    
graf23 = alt.Chart(generacion, title="% renovable").mark_arc().encode(
            alt.Theta('valor', aggregate='sum', type="quantitative")
                .title('Energía generada (GWh)'),
            alt.Color('tipo1', type='nominal')
                .title('Renovable')
            ).transform_filter(
                selection_ano
            ).transform_filter(
                {'not': alt.FieldEqualPredicate(field='tecnologia', equal='Generación total')}
            ).properties(
                width=160,
                height=200
            )   
    
    

output = alt.vconcat(
    alt.hconcat(graf11, graf12, graf13), 
    alt.hconcat(alt.hconcat(graf21, graf22),graf23).resolve_scale(color='independent')
).resolve_scale(color='independent')
output.save('Dashboard_energia_generada.html')
output

alt.VConcatChart(...)